In [9]:
import pandas as pd
import geopandas as gpd
import folium

## Reading data

In [13]:
df_ELEC_popCY = pd.read_csv('ELEC_popCY.csv'); df_ELEC_CY.head()

Region  2000       2001        2002        2003        2004        2005  \
0    ALAMEDA     0  72.472297  207.753918  322.743296  276.361026  231.911351   
1     ALPINE     0   0.289400    7.027114    2.233177    6.859183    1.642561   
2     AMADOR     0   0.011085   14.012635   18.680521   15.569109   15.569337   
3      BUTTE     0   8.433420   38.538256   66.344514   62.784402   55.459978   
4  CALAVERAS     0   0.011085   22.326980   41.455552   41.455578   41.455807   

         2006        2007        2008  ...        2012         2013  \
0  247.372107  306.316242  354.631107  ...  860.970889  2142.685534   
1    1.735203    1.881273    2.020836  ...    3.257038     7.051721   
2   18.680940   20.237033   17.116081  ...   17.114997    17.116081   
3   58.598724   61.817485   75.026501  ...   82.877897   100.063347   
4   36.674010   36.674385   31.954549  ...   39.849673    55.789542   

          2014         2015          2016          2017          2018  \
0  4330.382609  7977.214400  11218.173490  12769.898133  14174.057430   
1     0.000000     0.000000      0.000000      6.171725     13.265767   
2    10.893205    24.894673     31.117549     66.454642    111.701737   
3    88.055426   130.728439    165.329842    286.481076    435.650462   
4    25.503791    33.473725     44.631633     89.184506    144.260960   

          total        lat         lon  
0  72546.931365  37.609029 -121.899142  
1     81.504372  38.589393 -119.834501  
2    607.558192  38.449089 -120.591102  
3   2536.776820  39.651927 -121.585844  
4    985.907357  38.255818 -120.498149  

[5 rows x 23 columns]

## Reading the ward geodata

### ???  Issues ??
- the `CA_Counties_TIGER2016.geojson` file has been converted from following folder: (GeoJSON Data/ca-county-boundaries) which contains .shp .shx .dbf and so on but reading that with __folium.GeoJson__ into map would not yield any ward in next step. 
- the `gz_2010_us_050_00_5m.json` file yileds the wards but it is for whole USA and I just wish California. Also I would like to identify the column corresponding to each county so I can later key it on my own data and be able to make an interactive map with my own data

In [19]:
wards = gpd.read_file('GeoJSON Data\\mygeodata\\CA_Counties_TIGER2016.geojson')
# wards = gpd.read_file('GeoJSON Data\\gz_2010_us_050_00_5m.json')

## Below Making a sample map using a json data

In [14]:
california_center=(37.837769,-120.749135)

m = folium.Map(location`=california_center, zoom_start=8)
# folium.GeoJson(wards.to_json()).add_to(m)
# folium.GeoJson('GeoJSON Data\\mygeodata\\CA_Counties_TIGER2016.geojson').add_to(m)
folium.GeoJson('GeoJSON Data\\gz_2010_us_050_00_5m.json').add_to(m)
# folium.GeoJson((GeoJSON Data\\mygeodata\\CA_Counties_TIGER2016.geojson').add_to(m) ## it doesn't yield any ward

m.save('GeoJSON Datafolium_boundaries.html')

In [16]:
m.save('GeoJSON Datafolium_boundaries.html')
m

### Clipping the ward file to match the region names in the data (`here:ELEC_popCY['Region'`]

In [31]:
state_geo23=wards.sort_values(by=['NAME'])[:len(df_ELEC_popCY)]; state_geo23.head(2)

STATEFP COUNTYFP  COUNTYNS  GEOID     NAME        NAMELSAD LSAD CLASSFP  \
41      06      001  01675839  06001  Alameda  Alameda County   06      H1   
25      06      003  01675840  06003   Alpine   Alpine County   06      H1   

    MTFCC CSAFP CBSAFP METDIVFP FUNCSTAT       ALAND     AWATER     INTPTLAT  \
41  G4020   488  41860    36084        A  1914242789  212979931  +37.6471385   
25  G4020  None   None     None        A  1912292633   12557304  +38.6217831   

        INTPTLON                                           geometry  
41  -121.9124880  POLYGON ((-13612246.763 4538150.085, -13612346...  
25  -119.7983522  POLYGON ((-13366503.508 4678946.015, -13366492...

In [32]:
# state_geo23.to_json()

## Making colormap object

In [35]:
from branca.colormap import linear
import branca.colormap as cm

# ### OrRd colormap is kind of similar to tabelog score colors
# colormap = linear.RdBu.scale( df_ELEC_popCY['total'].min(), df_ELEC_popCY['total'].max() )
colormap = cm.LinearColormap(colors=['red','lightblue','blue'], 
                             index=[-200,0,1200],vmin=df_ELEC_popCY['total'].min(),vmax=df_ELEC_popCY['total'].max())

colors=df_ELEC_popCY['total'].apply(colormap)
colors.sample(3)

13    #0000ffff
1     #a1cae8ff
18    #0000ffff
Name: total, dtype: object

### ???  Issues ??
- Error !

In [36]:
m = folium.Map(location=california_center, #tiles='Stamen Toner',
                    zoom_start=11)
# wards_cali=wards[wards['STATEFP']=='06']
folium.GeoJson(
    state_geo23.to_json(),
    style_function=lambda feature: {
        'fillColor': colors.loc[features['NAME']],
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.8,
        'highlight': True
    }
).add_to(m)

# # folium.LayerControl().add_to(m)
m.add_child(colormap)
m.save('html/ward_choropleth_in_slides.html')
# #folium.LayerControl().add_to(m)

NameError: name 'features' is not defined

## Giving up on choropleth let's try if we can make the interactive map that highlights the ward when the mouse hover on it

### making folium map by keying on ward['Name'] data and data['Region] which suppose to be same from last step

### ???  Issues ??
- Error !

In [37]:
m = folium.Map(location=california_center, #tiles='Stamen Toner',
                    zoom_start=11)

# state_geo=('GeoJSON Data\\gz_2010_us_050_00_5m.json')
state_geo=state_geo23
state_data=df_ELEC_popCY
### Add the color for the chloropleth:
m.choropleth(
 geo_data=state_geo.to_json(),
 name='choropleth',
 data=state_data,
 columns=['Region','total'],
 key_on='features.NAME',
 
 fill_color='YlGn',
 fill_opacity=0.7,
 line_opacity=0.2,
 legend_name='Total number of electric vehicle',
 highlight=True
)
folium.LayerControl().add_to(m)
 
# Save to html
m.save('ELEC_Total_County.html')


C:\Users\Administrator\.conda\envs\Incubator37\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


AttributeError: 'NoneType' object has no attribute 'get'